# Bioinformatics Project - Computational Drug Discovery - Influenza virus A matrix protein M2  
Michael Bahchevanov  
***

## Feature Engineering 🚀  
This notebook will be looking into calculating the **molecular descriptors** and **fingerprints** via the *Morgan Fingerprint* which is a mathematically encoded *2048* bit vector. **Molecular fingerprints** are a way of encoding the structure of a molecule. They are most often represented in binary digits that represent the presence or absence of a particular substructure in the molecule. The molecular fingerprints are an essential part of the ***QSAR*** workflow and are a part of the fundamental cheminformatics tools for **virtual screening** and **mapping chemical space**. In particular, **substructure fingerprints** perform best for small molecules such as drugs (our target).  <br>[*QSAR-derived affinity fingerprints* - <a href="https://jcheminf.biomedcentral.com/track/pdf/10.1186/s13321-020-00444-5.pdf">Reference</a>, *Study on molecular fingerprints for drugs, biomolecules, and the metabolome* - <a href="https://jcheminf.biomedcentral.com/articles/10.1186/s13321-020-00445-4">Reference</a>]

We have already analyzed our data using the *EC50* measurement of concentration. This gave us a general overview of the bioactive binding compounds. Now our goal is to calculate the **molecular fingerprints**. As the *ChEMBL* database is well-maintained and somewhat standardized, for calculating the fingerprints we will be considering using also compounds with different measurements of *activation/inhibition*. Those would be namely:  
* EC$_{50}$ - Half maximal effective concentration  
* IC$_{50}$ - How much of a particular inhibitory substance (e.g. drug) is needed to inhibit, in vitro, a given biological process or biological component by 50%  
* K$_{i}$ - The concentration required to produce half maximum inhibition  
* K$_{d}$ - The equilibrium dissociation constant, which is used to evaluate and rank order strengths of interactions between two molecules, measurement for the binding affinity of a compound

There are two particular machine learning algorithms that have repeatedly shown consistent results (*AUCs* of around 0.7-0.8) - **Random Forests** and **Naive Bayes**. Although, for this preparation we will also be looking into **Random Matrix Theory** which is an algorithm framework (developed by <a href="https://www.alpha-lee.com/">Dr. Alpha Lee's group</a>) that promises high results.  <br>[*RMT, Alpha Lee Paper* - <a href="https://www.pnas.org/content/pnas/113/48/13564.full.pdf">Reference</a>]  <br> <br>
*Note - AUC stands for the area under the ROC (Receiver Operating Characteristic) curve. It is a graph showing the performance of a classification model at all classification thresholds and plots two parameters - True Positive and False Positive*  <br>
[<a href="https://machinelearningmastery.com/roc-curves-and-precision-recall-curves-for-classification-in-python/">Reference</a>]

### 1. Data Collection and Cleaning  
We will need 2 datasets:  
* a set of drugs that **bind** to a particular target (in our case the *Influenza virus A matrix protein M2*)  
* a set of drugs that **do not bind** to the particular target (a **decoy set**)  
For our **decoy set** we will be using the receptor used in <a href="https://www.pnas.org/content/pnas/113/48/13564.full.pdf">*Alpha Lee's Paper*</a> - *5HT1A*. The binding affinity to this receptor is irrelevant as we assume that the binding affinity to the *Influenza virus A matrix protein M2* is negligible (a reasonable assumption due to them being non-related). As we will be looking only for binder molecules, we will be selecting only the molecules that have a binding affinity of less that **1000nM**.  <br>
[<a href="https://towardsdatascience.com/random-matrix-theory-the-best-classifier-for-prediction-of-drug-binding-f82613fb48ed"> Reference</a>]

#### 1.1 Importing Libraries and Tooling 🔨  
We will be using *rdkit* for cheminformatics, *numpy* for computing, and *pandas* for data wrangling and loading. We will also need the *chembl_web_client* for querying the database.

In [1]:
import rdkit
from rdkit import Chem
from rdkit.Chem import PandasTools

import numpy as np
import pandas as pd

from chembl_webresource_client.new_client import new_client

In [2]:
import warnings
warnings.filterwarnings('ignore')

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

#### 1.2 Collecting the 5HT1A data from ChEMBL

In [3]:
target = new_client.target
query = target.search('5HT1A')
targets = pd.DataFrame.from_dict(query)
print(targets.shape)
targets

(9, 9)


cross_references           organism  \
0  [{'xref_id': 'P19327', 'xref_name': None, 'xre...  Rattus norvegicus   
1                                                 []  Rattus norvegicus   
2                                                 []  Rattus norvegicus   
3                                                 []  Rattus norvegicus   
4  [{'xref_id': 'P08908', 'xref_name': None, 'xre...       Homo sapiens   
5  [{'xref_id': 'NBK23263', 'xref_name': '5-HT1A ...       Mus musculus   
6                                                 []       Homo sapiens   
7                                                 []       Homo sapiens   
8                                                 []       Homo sapiens   

                                           pref_name  score  \
0                     Serotonin 1a (5-HT1a) receptor   24.0   
1                          Serotonin (5-HT) receptor   24.0   
2                       Serotonin 1 (5-HT1) receptor   24.0   
3  Serotonin 1a (5-HT1a) receptor/Adrenergic rece...   24.0   
4                     Serotonin 1a (5-HT1a) receptor   15.0   
5                     Serotonin 1a (5-HT1a) receptor   15.0   
6     Dopamine D2 receptor and serotonin 1a receptor   13.0   
7                       Serotonin 1 (5-HT1) receptor    8.0   
8                          Serotonin (5-HT) receptor    4.0   

   species_group_flag target_chembl_id  \
0               False        CHEMBL273   
1               False    CHEMBL2094123   
2               False    CHEMBL2095159   
3               False    CHEMBL2097171   
4               False        CHEMBL214   
5               False       CHEMBL3737   
6               False    CHEMBL2111460   
7               False    CHEMBL4524122   
8               False    CHEMBL2096904   

                                   target_components        target_type  \
0  [{'accession': 'P19327', 'component_descriptio...     SINGLE PROTEIN   
1  [{'accession': 'P35563', 'component_descriptio...     PROTEIN FAMILY   
2  [{'accession': 'P28564', 'component_descriptio...     PROTEIN FAMILY   
3  [{'accession': 'P15823', 'component_descriptio...  SELECTIVITY GROUP   
4  [{'accession': 'P08908', 'component_descriptio...     SINGLE PROTEIN   
5  [{'accession': 'Q64264', 'component_descriptio...     SINGLE PROTEIN   
6  [{'accession': 'P14416', 'component_descriptio...  SELECTIVITY GROUP   
7  [{'accession': 'P30939', 'component_descriptio...     PROTEIN FAMILY   
8  [{'accession': 'P30939', 'component_descriptio...     PROTEIN FAMILY   

   tax_id  
0   10116  
1   10116  
2   10116  
3   10116  
4    9606  
5   10090  
6    9606  
7    9606  
8    9606

We will be getting the **Single Protein** from index 4 - which denotes the receptor in humans.

In [4]:
selected_target = targets.target_chembl_id[4]
selected_target

'CHEMBL214'

In [5]:
activity = new_client.activity
res = activity.filter(target_chembl_id=selected_target)
df = pd.DataFrame.from_dict(res)
print(df.shape)
df.head(100)

(9899, 45)


activity_comment  activity_id activity_properties assay_chembl_id  \
0                 None        32187                  []    CHEMBL616136   
1                 None        32515                  []    CHEMBL849639   
2                 None        33363                  []    CHEMBL616136   
3                 None        34629                  []    CHEMBL616136   
4                 None        35741                  []    CHEMBL615755   
5                 None        35839                  []    CHEMBL616136   
6                 None        38320                  []    CHEMBL616136   
7                 None        44250                  []    CHEMBL616136   
8                 None        44514                  []    CHEMBL849639   
9                 None        45372                  []    CHEMBL616136   
10                None        45760                  []    CHEMBL616238   
11                None        48184                  []    CHEMBL849639   
12                None        49722                  []    CHEMBL616238   
13                None        50614                  []    CHEMBL616136   
14                None        50940                  []    CHEMBL849640   
15                None        54636                  []    CHEMBL849639   
16                None        59546                  []    CHEMBL849639   
17                None        60611                  []    CHEMBL616136   
18                None        60615                  []    CHEMBL616136   
19                None        61008                  []    CHEMBL849639   
20                None        61997                  []    CHEMBL616136   
21                None        62444                  []    CHEMBL616238   
22                None        63304                  []    CHEMBL616136   
23                None        67178                  []    CHEMBL616136   
24                None        68767                  []    CHEMBL849640   
25                None        69786                  []    CHEMBL616136   
26                None        70099                  []    CHEMBL849639   
27                None        71305                  []    CHEMBL849640   
28                None        73550                  []    CHEMBL616400   
29                None        75760                  []    CHEMBL616400   
30                None        75768                  []    CHEMBL616400   
31                None        77927                  []    CHEMBL616400   
32                None        79051                  []    CHEMBL616400   
33                None        79093                  []    CHEMBL616400   
34                None        80248                  []    CHEMBL857065   
35                None        80255                  []    CHEMBL616216   
36                None        80286                  []    CHEMBL616400   
37                None        80294                  []    CHEMBL616400   
38                None        82496                  []    CHEMBL616400   
39                None        89502                  []    CHEMBL616401   
40                None        89509                  []    CHEMBL616217   
41                None        89530                  []    CHEMBL616400   
42                None        91515                  []    CHEMBL616400   
43                None        98622                  []    CHEMBL616400   
44                None        99644                  []    CHEMBL872906   
45                None       103528                  []    CHEMBL616400   
46                None       103536                  []    CHEMBL616400   
47                None       104417                  []    CHEMBL616400   
48          Not Active       115090                  []    CHEMBL616371   
49          Not Active       117634                  []    CHEMBL616371   
50                None       117649                  []    CHEMBL616370   
51                None       118893                  []    CHEMBL616370   
52                None       11

In [6]:
df.to_csv('./data/5HT1A_01_bioactivity_data_raw.csv', index=False)

#### 1.3 Data Cleaning  
Now we will be creating a function that would normalize the values, drop null values, select only the entries who are recorded in **nM**, and finally drop the entries who do not have their **SMILES** notation, as we will be calculating the **Morgan Fingerprint** based on that notation.

In [7]:
def load_dataset(file, drop_non_binders=True, selected_metric=False):
    df = pd.read_csv(file, encoding = 'ISO-8859-1')
    
    # Drop NaNs in the affinity column
    df.reset_index(inplace=True)
    df.drop('index', axis=1, inplace=True)
    
    # Filtering for only activities recorded in nanomolar (nM) affinity
    if selected_metric:
        # Converting strings to floats and setting all non-numbers to NaN
        df['standard_value'] = pd.to_numeric(df['standard_value'], errors='coerce')
        df.dropna(subset=['standard_value'], inplace=True)
        df = df[df['standard_units'] == 'nM']
    
    # Dropping molecules that do not have a SMILES notation recorded
    df.dropna(subset=['canonical_smiles'])
    
    # Considering only the binders (affinity < 1000nM)
    if drop_non_binders:
        df = df[df['standard_value'] < 1000]
    
    # Dropping duplicate molecules
    df.drop_duplicates(subset=['canonical_smiles'], keep='first', inplace=True)
    
    return df

In [8]:
df_train_test = load_dataset('./data/influenza_virus_A_matrix_M2_protein_04_bioactivity_data_3class_pEC50.csv', drop_non_binders=False)
df_decoy = load_dataset('./data/5HT1A_01_bioactivity_data_raw.csv', drop_non_binders=False, selected_metric=True)

We will be saving these 2 datasets as a *.csv* file for further use.

In [9]:
df_train_test.to_csv('./data/influenza_virus_A_matrix_M2_protein_07_training_data.csv')
df_decoy.to_csv('./data/5HT1A_03_decoy_data.csv')

We are naming the bioactivity dataset for the *M2 matrix protein* as `train_test`. This is due to the fact that these are already compounds that have proven *inhibitory/activatory* response to the target protein. While our goal is to find compounds based on the **molecular fingerprint**, this data set is going to serve as our *validation* dataset.

In [10]:
df_train_test

molecule_chembl_id                                 canonical_smiles  \
0       CHEMBL4287824               N#CCCN(Cc1cccs1)S(=O)(=O)c1ccccc1F   
1       CHEMBL4277167             N#CCCN(Cc1cccs1)S(=O)(=O)c1cccc(F)c1   
2       CHEMBL4284419             N#CCCN(Cc1cccs1)S(=O)(=O)c1ccc(F)cc1   
3       CHEMBL4292316            N#CCCN(Cc1cccs1)S(=O)(=O)c1ccc(Cl)cc1   
4       CHEMBL4294990            N#CCCN(Cc1cccs1)S(=O)(=O)c1ccc(Br)cc1   
5       CHEMBL4286741             Cc1ccc(S(=O)(=O)N(CCC#N)Cc2cccs2)cc1   
6       CHEMBL4285916            COc1ccc(S(=O)(=O)N(CCC#N)Cc2cccs2)cc1   
7       CHEMBL4277990           N#CCCN(Cc1cccs1)S(=O)(=O)c1ccc(C#N)cc1   
8       CHEMBL4282531      N#CCCN(Cc1cccs1)S(=O)(=O)c1ccc(C(F)(F)F)cc1   
9       CHEMBL4293132  N#CCCN(Cc1cccs1)S(=O)(=O)c1ccc([N+](=O)[O-])cc1   
10      CHEMBL4292737        CC(=O)c1ccc(S(=O)(=O)N(CCC#N)Cc2cccs2)cc1   
11      CHEMBL4284865             N#CCCN(Cc1cccs1)S(=O)(=O)c1ccc(N)cc1   
12      CHEMBL4289324         O=S(=O)(c1ccc(Br)cc1)N(Cc1cccs1)Cc1cccs1   
13      CHEMBL4281445              CCCN(Cc1cccs1)S(=O)(=O)c1ccc(Br)cc1   
14      CHEMBL4281038       CCOC(=O)CCN(Cc1cccs1)S(=O)(=O)c1ccc(Br)cc1   
15      CHEMBL4291678         O=C(O)CCN(Cc1cccs1)S(=O)(=O)c1ccc(Br)cc1   
16      CHEMBL4290438             N#CCCN(Cc1ccco1)S(=O)(=O)c1ccc(F)cc1   
17      CHEMBL4279786            N#CCCN(Cc1ccco1)S(=O)(=O)c1ccc(Cl)cc1   
18      CHEMBL4293843            N#CCCN(Cc1ccco1)S(=O)(=O)c1ccc(Br)cc1   
19      CHEMBL4283250             Cc1ccc(S(=O)(=O)N(CCC#N)Cc2ccco2)cc1   
20      CHEMBL4283674            COc1ccc(S(=O)(=O)N(CCC#N)Cc2ccco2)cc1   
21      CHEMBL4291537           N#CCCN(Cc1ccco1)S(=O)(=O)c1ccc(C#N)cc1   
22      CHEMBL4287026      N#CCCN(Cc1ccco1)S(=O)(=O)c1ccc(C(F)(F)F)cc1   
23      CHEMBL4294934             Cc1cccc(S(=O)(=O)N(CCC#N)Cc2ccco2)c1   
24      CHEMBL4293428            N#CCCN(Cc1ccccc1)S(=O)(=O)c1ccc(F)cc1   
25      CHEMBL4283456         N#CCCN(Cc1ccc[nH]1)S(=O)(=O)c1ccc(Br)cc1   
26      CHEMBL4294025                 CCCN(CCC#N)S(=O)(=O)c1ccc(Br)cc1   
27          CHEMBL660                            NC12CC3CC(CC(C3)C1)C2   
28      CHEMBL4517321   Cc1cc(CNS(=O)(=O)c2ccc([N+](=O)[O-])cc2)c(C)o1   
29      CHEMBL4586595            Cc1cc(CNS(=O)(=O)c2ccc(C#N)cc2)c(C)o1   
30      CHEMBL4574356              Cc1cc(CNS(=O)(=O)c2ccc(F)cc2)c(C)o1   
31      CHEMBL4557215             Cc1cc(CNS(=O)(=O)c2ccc(Cl)cc2)c(C)o1   
32      CHEMBL4592186             Cc1cc(CNS(=O)(=O)c2ccc(Br)cc2)c(C)o1   
33      CHEMBL4590782         O=[N+]([O-])c1ccc(S(=O)(=O)NCc2ccoc2)cc1   
34      CHEMBL4518980   Cc1cc(CNS(=O)(=O)c2ccc([N+](=O)[O-])cc2)c(C)s1   
35      CHEMBL4557613            Cc1cc(CNS(=O)(=O)c2ccc(C#N)cc2)c(C)s1   
36      CHEMBL4586535             Cc1cc(CNS(=O)(=O)c2ccc(Cl)cc2)c(C)s1   
37      CHEMBL4527406             Cc1cc(CNS(=O)(=O)c2ccc(Br)cc2)c(C)s1   
38      CHEMBL4544193         O=[N+]([O-])c1ccc(S(=O)(=O)NCc2ccsc2)cc1   
39      CHEMBL4528685         O=[N+]([O-])c1ccc(S(=O)(=O)NCc2cccs2)cc1   
40      CHEMBL4534199   O=[N+]([O-])c1ccc(S(=O)(=O)NCc2csc3ccccc23)cc1   
41      CHEMBL4581693            N#Cc1ccc(S(=O)(=O)NCc2csc3ccccc23)cc1   
42      CHEMBL4588491              O=S(=O)(NCc1csc2ccccc12)c1ccc(F)cc1   
43      CHEMBL4579348             O=S(=O)(NCc1csc2ccccc12)c1ccc(Cl)cc1   
44      CHEMBL4527371             O=S(=O)(NCc1csc2ccccc12)c1ccc(Br)cc1   
45      CHEMBL4567651              Cc1ccc(S(=O)(=O)NCc2csc3ccccc23)cc1   
46      CHEMBL4538304         CC(=O)c1ccc(S(=O)(=O)NCc2csc3ccccc23)cc1   

           class       MW     LogP  NumHDonors  NumHAcceptors     pEC50  
0   intermediate  324.402  2.99178         0.0            4.0  5.537602  
1         active  324.402  2.99178         0.0            4.0  6.795880  
2         active  324.402  2.99178         0.0            4.0  6.853872  
3         active  340.857  3.50608         0.0            4.0  6.173925  
4         active  385.308  3.61518         0.0            4.0  6.376751  
5     

As for the **decoy**, it is assumed that it by no means has any relation to the responses in our target protein.

In [11]:
df_decoy.sample(100)

activity_comment  activity_id activity_properties assay_chembl_id  \
5248              NaN      3508313                  []   CHEMBL1259255   
39                NaN        89502                  []    CHEMBL616401   
1690              NaN      1027708                  []    CHEMBL615766   
4179              NaN      2603966                  []   CHEMBL1030618   
2072              NaN      1159665                  []    CHEMBL615470   
4191              NaN      2603978                  []   CHEMBL1030618   
9068              NaN     18899311                  []   CHEMBL4316413   
6304              NaN     12066665                  []   CHEMBL2162844   
4456              NaN      2948770                  []   CHEMBL1047377   
7270              NaN     15180231                  []   CHEMBL3404181   
5077              NaN      3433601                  []   CHEMBL1246632   
3647              NaN      2366466                  []   CHEMBL1035001   
7683              NaN     16486296                  []   CHEMBL3773936   
3173              NaN      1954456                  []    CHEMBL894423   
5169              NaN      3500712                  []   CHEMBL1260560   
603               NaN       476135                  []    CHEMBL616214   
4590              NaN      3090737                  []   CHEMBL1065705   
5067              NaN      3430813                  []   CHEMBL1248645   
5745              NaN      6190074                  []   CHEMBL1776882   
9370              NaN     19194765                  []   CHEMBL4390410   
788               NaN       602385                  []    CHEMBL616273   
9520              NaN     19283850                  []   CHEMBL4409660   
6958              NaN     14654872                  []   CHEMBL3269843   
2490              NaN      1507505                  []    CHEMBL852179   
989               NaN       697406                  []    CHEMBL615773   
4513              NaN      3087482                  []   CHEMBL1048564   
9077              NaN     18899320                  []   CHEMBL4316413   
8553              NaN     18530169                  []   CHEMBL4195132   
2003              NaN      1148058                  []    CHEMBL615753   
6131              NaN     10878902                  []   CHEMBL2026267   
865               NaN       648847                  []    CHEMBL615759   
1479              NaN       887887                  []    CHEMBL616226   
7927              NaN     16817124                  []   CHEMBL3871864   
646               NaN       507469                  []    CHEMBL615806   
217               NaN       342610                  []    CHEMBL615445   
7184              NaN     15089170                  []   CHEMBL3366226   
6987              NaN     14974910                  []   CHEMBL3374192   
8678              NaN     18571027                  []   CHEMBL4220993   
7708              NaN     16587955                  []   CHEMBL3806801   
9704              NaN     19431797                  []   CHEMBL4429161   
2725              NaN      1663336                  []    CHEMBL864517   
8736              NaN     18653242                  []   CHEMBL4229836   
8927              NaN     18858908                  []   CHEMBL4308345   
1974              NaN      1142599                  []    CHEMBL615975   
6932              NaN     14583569                  []   CHEMBL3243821   
8348              NaN     18278544                  []   CHEMBL4119506   
8819              NaN     18700563                  []   CHEMBL4254802   
7277              NaN     15180238                  []   CHEMBL3404181   
1011              NaN       703331                  []    CHEMBL615772   
2630              NaN      1660743                  []    CHEMBL859776   
9103              NaN     18997830                  []   CHEMBL4343018   
2213              NaN      1213497                  []    CHEMBL615805   
1707              NaN      1030387                  []    CHEMBL616225   
3640     

### 2. Generating the Molecular Fingerprint  
We are looking to convert the **molecular structure** into a **mathematical object**, to be able to apply machine learning algorithms on it. We will be encoding the **molecular structure** into a ***Morgan bit vector*** of length 2048. Each entry would be either the presence or absence of a particular chemical substructure.  
<img src="./assets/Morgan_Fingerprint.png"/>

In [12]:
def generate_morgan_matrix(smiles):
    morgan_matrix = np.zeros((1, 2048))
    l = len(smiles)
    
    # For each compound, get the structure, convert to Morgan fingerprint, and add to the morgan_matrix
    for i in range(l):
        try:
            compound = Chem.MolFromSmiles(smiles[i])
            fingerprint = Chem.AllChem.GetMorganFingerprintAsBitVect(compound, 2, nBits=2048)
            fingerprint = fingerprint.ToBitString()
            row = np.array([int(x) for x in list(fingerprint)])
            morgan_matrix = np.row_stack((morgan_matrix, row))
            
            # Progress checker
            if i % 500 == 0:
                percentage = np.round(100*(i/l), 1)
                print(f'{percentage}% done')
        except:
            print(f'problem at index: {i}')
    
    # Deleting the first row of zeros
    morgan_matrix = np.delete(morgan_matrix, 0, axis=0)
    
    print('\n')
    print(f'Morgan Matrix dimensions: {morgan_matrix.shape}')
    return morgan_matrix

In [18]:
morgan_matrix_train_test = generate_morgan_matrix(df_train_test.reset_index().canonical_smiles)
morgan_matrix_decoy = generate_morgan_matrix(df_decoy.reset_index().canonical_smiles)

0.0% done


Morgan Matrix dimensions: (47, 2048)
0.0% done
9.6% done
19.2% done
problem at index: 1392
28.8% done
38.5% done
48.1% done
57.7% done
67.3% done
76.9% done
86.5% done
96.1% done


Morgan Matrix dimensions: (5200, 2048)


The matrixes are of dimensions ***n x m*** where **n** denotes the number of molecules and **m** denotes the number of bit features (which are expected to be *2048* as the **Morgan bit vector** is of length 2048).  <br> <br>
Now, we will be saving the results of the **Morgan matrix** generation to a *.csv* file.

In [19]:
pd.DataFrame(morgan_matrix_train_test).to_csv('./data/influenza_virus_A_matrix_M2_protein_06_morgan_matrix.csv', index=False)
pd.DataFrame(morgan_matrix_decoy).to_csv('./data/5HT1A_02_morgan_matrix.csv', index=False)

### 3. Preparing the X and Y Data Matrices

#### 3.1 X Data Matrix

In [20]:
df_X = pd.DataFrame(morgan_matrix_train_test)
df_X

0    1    2    3    4    5    6    7    8    9   10   11   12   13   14  \
0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
1   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
2   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
3   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
4   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
5   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
6   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
7   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
8   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
9   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
10  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
11  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
12  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
13  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
14  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
15  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
16  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
17  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
18  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
19  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
20  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
21  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
24  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
26  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
27  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
28  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
29  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
30  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
31  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
32  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
33  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
34  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
35  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
36  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
37  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
38  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
39  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
40  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
41  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
42  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
43  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
44  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
45  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
46  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

     15   16   17   18   19   20   21   22   23   24   25   26   27   28   29  \
0   0.0  0.0  1.0  0.0  0.0  0.0  0.

#### 3.2 Y Variable

In [21]:
df_y = pd.read_csv('./data/influenza_virus_A_matrix_M2_protein_04_bioactivity_data_3class_pEC50.csv')['pEC50']
df_y

0     5.537602
1     6.795880
2     6.853872
3     6.173925
4     6.376751
5     6.251812
6     5.111821
7     8.096910
8     5.142065
9     4.977572
10    4.395990
11    5.142065
12    5.401209
13    6.431798
14    5.459671
15    3.973222
16    6.259637
17    6.113509
18    4.944240
19    6.408935
20    4.673050
21    6.494850
22    4.062934
23    5.140862
24    6.356547
25    6.022276
26    4.764219
27    6.180456
28    5.767004
29    4.894831
30    4.619789
31    5.512862
32    5.332547
33    4.088949
34    5.655608
35    5.853872
36    5.966576
37    5.801343
38    5.623423
39    5.696804
40    5.463442
41    4.340369
42    5.206210
43    5.273273
44    4.816730
45    4.644357
46    4.556111
Name: pEC50, dtype: float64

#### 3.3 Combing X and Y

In [22]:
df_combined = pd.concat([df_X, df_y], axis=1)
df_combined

0    1    2    3    4    5    6    7    8    9   10   11   12   13   14  \
0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
1   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
2   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
3   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
4   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
5   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
6   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
7   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
8   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
9   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
10  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
11  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
12  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
13  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
14  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
15  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
16  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
17  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
18  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
19  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
20  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
21  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
22  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
23  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
24  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
25  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
26  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
27  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
28  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
29  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
30  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
31  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
32  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
33  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
34  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
35  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
36  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
37  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
38  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
39  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
40  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
41  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
42  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
43  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
44  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
45  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
46  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

     15   16   17   18   19   20   21   22   23   24   25   26   27   28   29  \
0   0.0  0.0  1.0  0.0  0.0  0.0  0.

Now, we will be saving the combined dataset as a *.csv* file that we are later going to use for model building.

In [23]:
df_combined.to_csv('./data/influenza_virus_A_matrix_M2_protein_08_morgan_matrix_fingerprint.csv', index=False)

*** 
### Overview
In this notebook we have mathematically encoded the **molecular structure** of our target protein, *Influenza virus A matrix M2 protein*. We have also collected and cleaned a **decoy** set that would serve for modelling later. The **decoy** set consists of the *5HT1A* receptor in humans for which we have also applied the same encoding technique as for our target protein. We have also prepared the targeted protein dataset for model building. In the next notebook, we will be building the model.